In [1]:
import numpy as np
import pandas as pd
import tensorflow as tf
import matplotlib.pyplot as plt
import seaborn as sns
import re, string
import nltk
from sklearn import preprocessing
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression

from transformers import BertTokenizerFast
from transformers import TFBertModel

import tensorflow as tf

In [2]:
df_train = pd.read_csv("train.csv")
df_test = pd.read_csv("test.csv")

train_dataset = df_train.dropna()
test_dataset = df_test.dropna()

train_dataset = train_dataset.sample(frac=0.4)
test_dataset = test_dataset.sample(frac=0.4)

In [3]:
df_train['usefulCount'].describe()

count    160398.000000
mean         28.097613
std          36.457876
min           0.000000
25%           6.000000
50%          16.000000
75%          36.000000
max        1291.000000
Name: usefulCount, dtype: float64

In [4]:
df_test['usefulCount'].describe()

count    53471.000000
mean        28.083634
std         36.231706
min          0.000000
25%          6.000000
50%         16.000000
75%         36.000000
max        949.000000
Name: usefulCount, dtype: float64

In [5]:
train_dataset.shape

(64156, 5)

In [6]:
test_dataset.shape

(21387, 5)

In [7]:
tokenizer = BertTokenizerFast.from_pretrained('bert-base-uncased')

In [8]:
x_train = train_dataset['text'].values
y_train = train_dataset['sentiment'].values
x_train, x_valid, y_train, y_valid = train_test_split(x_train, y_train, test_size=0.3, stratify=y_train, random_state=43, shuffle=True)
x_test = test_dataset['text'].values
y_test = test_dataset['sentiment'].values

print(f"Train Count: {x_train.shape}\nValidation Count: {x_valid.shape}\nTest Count: {x_test.shape}")

Train Count: (44909,)
Validation Count: (19247,)
Test Count: (21387,)


In [9]:
ohe = preprocessing.OneHotEncoder()
y_train = ohe.fit_transform(np.array(y_train).reshape(-1, 1)).toarray()
y_valid = ohe.fit_transform(np.array(y_valid).reshape(-1, 1)).toarray()

print(y_train.shape)
print(y_valid.shape)

(44909, 3)
(19247, 3)


In [10]:
tokenizer = BertTokenizerFast.from_pretrained('bert-base-uncased')

In [11]:
MAX_LEN=128

def bert_tokenize(data,max_len=MAX_LEN) :
    input_ids = []
    attention_masks = []
    for text in data:
        encoded = tokenizer.encode_plus(
            text,
            add_special_tokens=True,
            truncation='only_first',
            max_length=max_len,
            padding='max_length',
            return_attention_mask=True
        )
        input_ids.append(np.array(encoded['input_ids']))
        attention_masks.append(np.array(encoded['attention_mask']))
    return np.array(input_ids),np.array(attention_masks)

In [12]:
train_input_ids, train_attention_masks = bert_tokenize(x_train, MAX_LEN)
val_input_ids, val_attention_masks = bert_tokenize(x_valid, MAX_LEN)
test_input_ids, test_attention_masks = bert_tokenize(x_test, MAX_LEN)

Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg option direction
Ignored unknown kwarg opt

In [13]:
bert_model = TFBertModel.from_pretrained('bert-base-uncased')

def create_model(bert_model, max_len=MAX_LEN):
    
    ##params###
    opt = tf.keras.optimizers.Adam(learning_rate=2e-5, decay=1e-7)
    loss = tf.keras.losses.CategoricalCrossentropy()
    accuracy = tf.keras.metrics.CategoricalAccuracy()


    input_ids = tf.keras.Input(shape=(max_len,),dtype='int32')
    
    attention_masks = tf.keras.Input(shape=(max_len,),dtype='int32')
    
    embeddings = bert_model([input_ids,attention_masks])[1]
    
    output = tf.keras.layers.Dense(3, activation="softmax")(embeddings)
    
    model = tf.keras.models.Model(inputs = [input_ids,attention_masks], outputs = output)
    
    model.compile(opt, loss=loss, metrics=accuracy)
    
    
    return model

Metal device set to: Apple M1 Pro

systemMemory: 16.00 GB
maxCacheSize: 5.33 GB



2022-03-13 09:22:23.826640: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:305] Could not identify NUMA node of platform GPU ID 0, defaulting to 0. Your kernel may not have been built with NUMA support.
2022-03-13 09:22:23.826750: I tensorflow/core/common_runtime/pluggable_device/pluggable_device_factory.cc:271] Created TensorFlow device (/job:localhost/replica:0/task:0/device:GPU:0 with 0 MB memory) -> physical PluggableDevice (device: 0, name: METAL, pci bus id: <undefined>)
Some layers from the model checkpoint at bert-base-uncased were not used when initializing TFBertModel: ['mlm___cls', 'nsp___cls']
- This IS expected if you are initializing TFBertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFBertModel from the checkpoint of a model that you expect to be exactly identi

In [14]:
model = create_model(bert_model, MAX_LEN)
model.summary()

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_1 (InputLayer)           [(None, 128)]        0           []                               
                                                                                                  
 input_2 (InputLayer)           [(None, 128)]        0           []                               
                                                                                                  
 tf_bert_model (TFBertModel)    TFBaseModelOutputWi  109482240   ['input_1[0][0]',                
                                thPoolingAndCrossAt               'input_2[0][0]']                
                                tentions(last_hidde                                               
                                n_state=(None, 128,                                           

In [15]:
EPOCHS = 3
BATCH_SIZE = 64
checkpoint_filepath = 'BERT_128'
model_checkpoint_callback = tf.keras.callbacks.ModelCheckpoint(
    filepath=checkpoint_filepath,
    save_weights_only=True,
    monitor='val_categorical_accuracy',
    mode='max',
    save_best_only=True)

train_history = model.fit([train_input_ids,train_attention_masks], 
                          y_train, 
                          validation_data=([val_input_ids,val_attention_masks], y_valid),
                          epochs=EPOCHS, 
                          batch_size=BATCH_SIZE,
                          callbacks=[model_checkpoint_callback])

Epoch 1/3


2022-03-13 09:22:26.907861: W tensorflow/core/platform/profile_utils/cpu_utils.cc:128] Failed to get CPU frequency: 0 Hz
2022-03-13 09:22:30.390623: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


702/702 [==============================] - ETA: 0s - loss: 0.6280 - categorical_accuracy: 0.7533

2022-03-13 10:04:05.843611: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


702/702 [==============================] - 2713s 4s/step - loss: 0.6280 - categorical_accuracy: 0.7533 - val_loss: 0.5358 - val_categorical_accuracy: 0.7879
Epoch 2/3
702/702 [==============================] - 2833s 4s/step - loss: 0.4613 - categorical_accuracy: 0.8191 - val_loss: 0.5020 - val_categorical_accuracy: 0.8075
Epoch 3/3
702/702 [==============================] - 2840s 4s/step - loss: 0.3431 - categorical_accuracy: 0.8658 - val_loss: 0.5614 - val_categorical_accuracy: 0.8015


In [16]:
y_pred = model.predict([test_input_ids,test_attention_masks])
y_pred = np.argmax(y_pred, axis=1)
y_pred = pd.DataFrame(y_pred,columns=['label'])
y_pred = y_pred['label'].map(\
             {0:-1,1:0,2:1})

2022-03-13 11:42:13.944029: I tensorflow/core/grappler/optimizers/custom_graph_optimizer_registry.cc:113] Plugin optimizer for device_type GPU is enabled.


In [19]:
from sklearn.metrics import accuracy_score, f1_score
accuracy = accuracy_score(y_test,y_pred)
accuracy

0.8053022864356852

In [21]:
f1 = f1_score(y_test,y_pred,average='macro')
f1

0.6849430036411123